# Spotify Analytics - Modern Data Architectures for Big Data II

- Constança Drago Braga 
- Alexander Gross
- Khaled Mahmoud
- Diego Mata Saravia 
- Orlando Montalvo Puccini 
- Nadine Raad
- Guillermo Palacín Gómez 

<img width="200" style="float:left" src="https://upload.wikimedia.org/wikipedia/commons/thumb/2/26/Spotify_logo_with_text.svg/2560px-Spotify_logo_with_text.svg.png" />

## Description

Team D of section 2 are here to **change the way we listen music in group.** Sometimes when we go to parties with people from the master, we dont know which is the perfect song/playlist to put in the party. Some like a style of music, others like specific music from a country, others like more international music. Which makes it difficult to choose which song to play at the parties.

**Wouldn't it be great if we use all the tools we have learn in the subject to solve that problem?**

Keep reading!

## The Challenge 

To solve the challenge we will use: Graph processing, Machine Learning processing and Stream processing. 

- Firstly, we will gather all the information of all the songs inside the playlist from 26 persons of the master of Spotify, and we will ingest them in HDFS under the directory ``/datalake/raw/spotify/users/<user_id>/<playlist_id>``.


- Secondly, we will extract all the features of a song and we will save them in HDFS under the directory ``/datalake/raw/spotify/users/song_features``. The features of a songs are difined by potify by atributes like acousticness, danceability, instrumentalness... [Link to song features](https://developer.spotify.com/documentation/web-api/reference/#/operations/get-audio-features)


- Once we have ingested all the songs and song_features, we will use Spark GraphFrames and we will compute the page rank (see Secion 1) to see what are the most popular songs. 


- Here it comes the fun: We will use the value of pageRank as a target variable and we will train our own model to be able to predict the page rank, hence the popularity of a song inside the master, using **Spark ML**. The model will be saved in HDFS. 


- Fun++; Spark Streaming in Action:  When user is playing a song, the information of the current song will be stored in Kafka topics and will be consumed by Spark. We will apply our previously created model to the current song.  If the predicted value of the pageRank is high the song will be added to the playlist of the master (created specifically for the purpose of this project) https://open.spotify.com/playlist/4JJmlxODSah5VYAoqGeOqR


Even though we have used the project using samples of people from the master, this use case can be easily extrapolated to a music club where, they have the Spotify profiles of the people inside. 

## Project folder structure 

The project folder is structured in the following way: 

   --``ingestion_spotify.ipynb``: Is the notebook to run the batch ingestion from the spotify API
   
   -- ``usernames.yaml``: Contains the public username and the name of the profiles of Spotify from people of our master. 
   
   -- ``credentials.json``: Contains the cliend_id, the client_secret and the access token of our developer account of spotify: 
       We have created an Spotify Account for this project: 
       
           - username: 31bjwtgzdfvpauztihztufpez2gi
           - password: osbdet123$
   -- ``oauth2_spotify.py``:  To add songs to playlist and to track the current state of the player, Spotify, requires oauth authorization. When launched it creates a webserver ``http://localhost:8088/modern-data`` with the redicrect URI needed in order to get the access token. Once we have the access token it will be saved in the ``credentials.json`` file.
   
   -- ``kafka-spotify-producer.py``: Sends the current song being played in our Spotify account to the toppic ``spotify_mbd`` and sends the featutes of that song to the topic ``spotify_mbd_features``
   
   -- ``kafka_consumer_v2.py``: Will listen in the ``send_to_playlist`` topic. Spark  Streaming will send to that toppic all the songs where the predicted value of the pageRank is bigger than our threshold. The consumer will be in charge of adding them to the playlist of the master (https://open.spotify.com/playlist/4JJmlxODSah5VYAoqGeOqR)
  
   

#### Having that said, let's start
# 0. Setup. 

Before running the notebook please make sure that: 

- Kafka service is running: ``sudo service kafka start``

- run ``python3 oauth2_spotify.py`` and type http://localhost:8088/modern-data this will save the access token in the credentials folder. 
    
- Start hadoop: ``hadoop-start.sh``


### 0.1 Search for Spark Installation 
    
   

In [1]:
import findspark
findspark.init()

In [2]:
import pandas as pd
pd.set_option('display.max_colwidth', None)

<a id='0.2'></a>
### 0.2 Create SparkSession

By setting this environment variable we can include extra libraries in our Spark cluster.<br/>
GraphFrames is not in spark core so we have to add it this way

In [3]:
import os
os.environ['PYSPARK_SUBMIT_ARGS'] = '--packages org.apache.spark:spark-sql-kafka-0-10_2.12:3.0.3,graphframes:graphframes:0.8.2-spark3.2-s_2.12 --jars "/usr/share/java/mariadb-java-client.jar,/opt/hive3/lib/hive-hcatalog-core-3.1.2.jar" pyspark-shell'

The first thing always is to create the SparkSession

In [4]:
from pyspark.sql.session import SparkSession

spark = (SparkSession.builder
    .appName("Spotify Analytics")
    .config("spark.sql.warehouse.dir","hdfs://localhost:9000/warehouse")
    .enableHiveSupport()
    .getOrCreate())

Ivy Default Cache set to: /home/osbdet/.ivy2/cache
The jars for the packages stored in: /home/osbdet/.ivy2/jars
:: loading settings :: url = jar:file:/opt/spark3/jars/ivy-2.4.0.jar!/org/apache/ivy/core/settings/ivysettings.xml
org.apache.spark#spark-sql-kafka-0-10_2.12 added as a dependency
graphframes#graphframes added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-6e97a313-d687-40a8-854a-2f1c3d34cf85;1.0
	confs: [default]
	found org.apache.spark#spark-sql-kafka-0-10_2.12;3.0.3 in central
	found org.apache.spark#spark-token-provider-kafka-0-10_2.12;3.0.3 in central
	found org.apache.kafka#kafka-clients;2.4.1 in central
	found com.github.luben#zstd-jni;1.4.4-3 in central
	found org.lz4#lz4-java;1.7.1 in central
	found org.xerial.snappy#snappy-java;1.1.8.2 in central
	found org.slf4j#slf4j-api;1.7.30 in central
	found org.spark-project.spark#unused;1.0.0 in central
	found org.apache.commons#commons-pool2;2.6.2 in central
	found graphframes#graphframes;

## Part 1.  Graph Processing

We will start reading all the songs from all the playlists from the students of the masters 

In [5]:
paylists = (spark.read
            .option("header","true")
            .option("inferSchema","true")
            .json("hdfs://localhost:9000/datalake/raw/spotify/users/*"))

Lets see what is the structure of the playlists

In [6]:
paylists.printSchema()

root
 |-- collaborative: boolean (nullable = true)
 |-- description: string (nullable = true)
 |-- external_urls: struct (nullable = true)
 |    |-- spotify: string (nullable = true)
 |-- followers: struct (nullable = true)
 |    |-- href: string (nullable = true)
 |    |-- total: long (nullable = true)
 |-- href: string (nullable = true)
 |-- id: string (nullable = true)
 |-- images: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- height: long (nullable = true)
 |    |    |-- url: string (nullable = true)
 |    |    |-- width: long (nullable = true)
 |-- name: string (nullable = true)
 |-- owner: struct (nullable = true)
 |    |-- display_name: string (nullable = true)
 |    |-- external_urls: struct (nullable = true)
 |    |    |-- spotify: string (nullable = true)
 |    |-- href: string (nullable = true)
 |    |-- id: string (nullable = true)
 |    |-- type: string (nullable = true)
 |    |-- uri: string (nullable = true)
 |-- primary_color: st

As shown, when we transform the json into the dataframe, it looks very ugly 😭 All the information, is contained in the tracks field. 
Lets make the DF pretty 😃

In [7]:
paylists.limit(5).toPandas()

collaborative  \
0          False   
1          False   
2          False   
3          False   
4          False   

                                                    description  \
0                                                                 
1                                                                 
2                  Upbeat dance pop to keep your heart pumping.   
3  Uplifting and energetic music that helps you stay motivated.   
4                                                                 

                                                 external_urls  \
0  (https://open.spotify.com/playlist/4HkQ7NMIekzMCtRnq6yhoM,)   
1  (https://open.spotify.com/playlist/0JRpsXgVgOPkVJDrAi6EpK,)   
2  (https://open.spotify.com/playlist/37i9dQZF1DWSJHnPb1f0X3,)   
3  (https://open.spotify.com/playlist/37i9dQZF1DXdxcBWuJkbcy,)   
4  (https://open.spotify.com/playlist/1sXIRwLyRvy0nGWTOQYVFn,)   

         followers  \
0    (None, 10895)   
1       (None, 58)   
2  (None, 3462362)   
3  (None, 6184504)   
4        (None, 2)   

                                                          href  \
0  https://api.spotify.com/v1/playlists/4HkQ7NMIekzMCtRnq6yhoM   
1  https://api.spotify.com/v1/playlists/0JRpsXgVgOPkVJDrAi6EpK   
2  https://api.spotify.com/v1/playlists/37i9dQZF1DWSJHnPb1f0X3   
3  https://api.spotify.com/v1/playlists/37i9dQZF1DXdxcBWuJkbcy   
4  https://api.spotify.com/v1/playlists/1sXIRwLyRvy0nGWTOQYVFn   

                       id  \
0  4HkQ7NMIekzMCtRnq6yhoM   
1  0JRpsXgVgOPkVJDrAi6EpK   
2  37i9dQZF1DWSJHnPb1f0X3   
3  37i9dQZF1DXdxcBWuJkbcy   
4  1sXIRwLyRvy0nGWTOQYVFn   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     images  \
0  [(640, https://mosaic.scdn.co/640/ab67616d0000b27321ee2e52263690b0b2c80c2aab67616d0000b273722d2b3531903685d240a4b0ab67616d0000b273922a7339d969b5f0262580f5ab67616d0000b273aa3bbf26a1ff6343348f501d, 640), (300, https://mosaic.scdn.co/300/ab67616d0000b27321ee2e52263690b0b2c80c2aab67616d0000b273722d2b3531903685d240a4b0ab67616d0000b273922a7339d969b5f0262580f5ab67616d0000b273aa3bbf26a1ff6343348f501d, 300), (60, https://mosaic.scdn.co/60/ab67616d0000b27321ee2e52263690b0b2c80c2aab67616d0000b273722d2b3531903685d240a4b0ab67616d0000b273922a7339d969b5f0262580f5ab67616d0000b273aa3bbf26a1ff6343348f501d, 60)]   
1  [(640, https://mosaic.scdn.co/640/ab67616d0000b2731604036fd148c874c4c71956ab67616d0000b27348d52534e806adb2a5d8d862ab67616d0000b273545c930fa9fada545b01f71dab67616d0000b273df1678b77ddb9f7f12636a5c, 640), (300, https://mosaic.scdn.co/300/ab67616d0000b2731604036fd148c874c4c71956ab67616d0000b27348d52534e806adb2a5d8d862ab67616d0000b273545c930fa9fada545b01f71dab67616d0000b273df1678b77ddb9f7f12636a5c, 300), (60, https://mosaic.scdn.co/60/ab67616d0000b2731604036fd148c874c4c71956ab67616d0000b27348d52534e806adb2a5d8d862ab67616d0000b273545c930fa9fada545b01f71dab67616d0000b273df1678b77ddb9f7f12636a5c, 60)]   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          [(None, https://i.scdn.co/image/a

We will use explode function, to have one track per row, and we will select the relevant attributes. The DF starts looking nicer :) 

In [8]:
tracks = paylists.selectExpr('id as playlist_id', 'followers.total as followers','owner.id owner_id', 
                             'explode(tracks.items) as track', 'name as playlist_name', 
                             'user_playlist_id', 'user_name')
tracks.limit(5).toPandas()

playlist_id  followers    owner_id  \
0  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424   
1  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424   
2  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424   
3  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424   
4  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          track  \
0                                                                                                                                                                                                                                                                 (2021-10-12T19:40:47Z, ((https://open.spotify.com/user/1110657424,), https://api.spotify.com/v1/users/1110657424, 1110657424, user, spotify:user:1110657424), Fa

Tracks still has a lot of information that we do not need. Also we are going to separate the list of artist with a ',' using concat_ws function

In [9]:
from pyspark.sql.functions import concat_ws, col

tracks = tracks.selectExpr("*", "track.track.album.artists.name as artists", "track.track.name as name_song ") \
                .withColumn("artists_names", concat_ws(", ",col("artists"))) \
                .withColumn("song_id", col("track.track.id"))\
                .withColumn("popularity", col("track.track.popularity"))\
                .withColumn("duration_ms", col("track.track.duration_ms"))\
                .drop("track")\
                .drop("artists")

tracks.limit(5).toPandas()

playlist_id  followers    owner_id   playlist_name  \
0  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424  Reggaeton 2022   
1  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424  Reggaeton 2022   
2  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424  Reggaeton 2022   
3  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424  Reggaeton 2022   
4  4HkQ7NMIekzMCtRnq6yhoM      10895  1110657424  Reggaeton 2022   

  user_playlist_id       user_name        name_song   artists_names  \
0    jecrespo.2012  Juan Francisco        SEJODIOTO         KAROL G   
1    jecrespo.2012  Juan Francisco  Dile (Homenaje)     Jhay Cortez   
2    jecrespo.2012  Juan Francisco      Experimento     Myke Towers   
3    jecrespo.2012  Juan Francisco         Una Nota        J Balvin   
4    jecrespo.2012  Juan Francisco           Cúrame  Rauw Alejandro   

                  song_id  popularity  duration_ms  
0  704LUEih663hiE3CnyUrFW          88       181106  
1  073yIM7v2j6XadD4Nkn0Fh          82       228933  
2  6c32C8T3KlXrbvWSoD5aON          85       222728  
3  7iqOIHHEmu6Vhw25GgQ2eA          85       170760  
4  3PwRuzdphgedcWVUOVYJ7I          65       164705

In [10]:
tracks.dtypes

[('playlist_id', 'string'),
 ('followers', 'bigint'),
 ('owner_id', 'string'),
 ('playlist_name', 'string'),
 ('user_playlist_id', 'string'),
 ('user_name', 'string'),
 ('name_song', 'string'),
 ('artists_names', 'string'),
 ('song_id', 'string'),
 ('popularity', 'bigint'),
 ('duration_ms', 'bigint')]

What are the most repeated songs among all the students ? 

In [11]:
from pyspark.sql.functions import desc


aux_songs = tracks.groupBy("name_song", "song_id").count()
aux_songs = aux_songs.orderBy(desc("count")).where("name_song!='null'").withColumnRenamed("song_id", "id")
aux_songs.limit(5).toPandas()

name_song  \
0  Todo Lo Que Quieres Es Bailar (feat. Descemer Bueno)   
1                                              Caraluna   
2                                                Closer   
3                             Otra vez (feat. J Balvin)   
4                                     Seve - Radio Edit   

                       id  count  
0  5mwkN6uECjhgmIS19ctXO1     10  
1  4XTMj7kd8DHLl0r7ghmEAr      8  
2  7BKLCZ1jbUBVqRi2FVlTVw      8  
3  7pk3EpFtmsOdj8iUhjmeCM      8  
4  6UqRGwjwYL0stXbaodTxwo      8

We will use this table later to join the id of the user with their name after the Graph. 


In [12]:
aux_users = tracks.groupBy("user_name", "user_playlist_id").sum()
aux_users = aux_users.where("user_name!='null'").withColumnRenamed("user_playlist_id", "id")\
            .select("user_name", "id").orderBy(desc("user_name"))
aux_users.limit(5).toPandas()

user_name                         id
0         Thomas S                 1150346509
1          Quirijn                 marjolein2
2  Patrick Rossier                 1130794884
3        Orlando M               orlomontalvo
4    Nour Darwiche  22ci4w44lamfcdfyrzmk2m5fi

Ummm... Lets see what are the name of the playlist that our colleage Orlando has in his spotify account. Should we follow any of them? He has a good taste in music. 

In [13]:
tracks.select("playlist_name").where(col("owner_id")=='orlomontalvo').distinct().show()

+----------------+
|   playlist_name|
+----------------+
|           JRMS1|
|             ITA|
|             RES|
|             UKS|
|            RHCP|
|My Shazam Tracks|
|            JRMS|
+----------------+



-- But... Team D,  you mention something about Graphs, where are they?

-- Wait wait, we are on our way. 

Our nodes will be formed by both songs_id and users_id. (Graphframes does not allow us to have different types of nodes)

Our edges will have as users as source and songs as a destination (all incoming connections from a song will come from users)

In [14]:
# changing the user_id to src and song_id to dst
edges = tracks.select("*").withColumnRenamed("user_playlist_id", "src")\
                          .withColumnRenamed("song_id", "dst")

edges = edges.groupBy("src", "dst", "name_song").agg({'duration_ms':'sum', 'src': 'count'})\
                        .withColumnRenamed("count(src)", "count")\
                        .withColumnRenamed("sum(duration_ms)", "sum_ms")
# Dropping songs with null values
edges = edges.where("src != 'null' AND dst != 'null' ")


edges.orderBy(desc("count")).show()

+--------------+--------------------+--------------------+-------+-----+
|           src|                 dst|           name_song| sum_ms|count|
+--------------+--------------------+--------------------+-------+-----+
|   12129417609|48svUiwMMYQRPyesV...|     Tabaco Y Chanel|1562000|    5|
|   12129417609|1T7CJOqK5gcp3WUNO...|Entre Mi Vida y l...| 704744|    4|
|   anasofiarod|0CrQ7dNvGPXmex621...|         Te Encontre| 838532|    4|
|     126584446|4Ld3RS6KBXGsvtfmn...|El Perdón (with E...| 828052|    4|
|     126584446|74Oqp9YxCMHaS4A57...|Rubia Sol Morena ...| 699520|    4|
|mariacostalima|0hhXziDUO0wNYPsst...|           Overnight| 878416|    4|
|mariacostalima|1qtiESAzfGMw3YqJv...|           Lightenup| 948908|    4|
|   anasofiarod|36uiMu91qIsehdmnt...|Le Hace Falta Un ...| 818140|    4|
|   12129417609|2jNqxXMkVVpEvjvvw...|       Dejame Entrar| 963040|    4|
|     126584446|720UzNnKdJIYHwhWh...|      Ganas de Verte| 799304|    4|
|   12129417609|10w7J6oGWd8mqQbls...|Lo Que Dejaste

In [15]:
nodes_1 = tracks.select(col("user_playlist_id"))
nodes_2 = tracks.select(col("song_id"))
# Nodes = People +  Song

nodes = nodes_1.union(nodes_2).distinct().orderBy(desc("user_playlist_id"))\
                                .withColumnRenamed("user_playlist_id", "id")

nodes.na.drop()
nodes.show(5)

+--------------------+
|                  id|
+--------------------+
|        orlomontalvo|
|          marjolein2|
|      mariacostalima|
|       jecrespo.2012|
|gtdn4wkr2vw7bl5td...|
+--------------------+
only showing top 5 rows



In [16]:
from graphframes import GraphFrame

graph = GraphFrame(nodes, edges)

graph.cache()

GraphFrame(v:[id: string], e:[src: string, dst: string ... 3 more fields])

 #### What are the most listened songs (the ones with more inDegrees)? 

A lot of reggeton in our master...

In [17]:
from pyspark.sql.functions import asc

inDeg = (graph.inDegrees).join(aux_songs, "id")
inDeg.orderBy(desc("inDegree")).limit(10).toPandas()

id  inDegree                              name_song  \
0  6UqRGwjwYL0stXbaodTxwo         7                      Seve - Radio Edit   
1  5TMLavqGRKNxgzMBrVpC9R         7                      Mon Amour - Remix   
2  7BKLCZ1jbUBVqRi2FVlTVw         6                                 Closer   
3  5mey7CLLuFToM2P68Qu1gF         6                     Andas En Mi Cabeza   
4  7pk3EpFtmsOdj8iUhjmeCM         6              Otra vez (feat. J Balvin)   
5  3umS4y3uQDkqekNjVpiRUs         5                              El Amante   
6  6YZdkObH88npeKrrkb8Ggf         5         DUELE EL CORAZON (feat. Wisin)   
7  0bdL8X3MrX51dRz231BFtv         5  Moviendo Caderas (feat. Daddy Yankee)   
8  5fwSHlTEWpluwOM0Sxnh5k         5                                  Pepas   
9  75JFxkI2RXiU7L9VXzMkle         5                          The Scientist   

   count  
0      8  
1      8  
2      8  
3      7  
4      8  
5      6  
6      5  
7      5  
8      5  
9      5

Who are the users that listen to more songs? 

**Wow! Big price for Ivan Humbert with 1940 songs!** Section 2 is almost leading this podium 

In [18]:
from pyspark.sql.functions import asc


outDeg = (graph.outDegrees).join(aux_users, "id")
outDeg.orderBy(desc("outDegree")).limit(5).toPandas()

id  outDegree              user_name
0      126584446       1681           Ivan Humbert
1    12129417609       1340  Juan Manuel Maldonado
2      124716254       1310         Miguel Hopkins
3  jecrespo.2012       1155         Juan Francisco
4     1130794884        938        Patrick Rossier

Lets create our pagerank feature

In [19]:
ranks = graph.pageRank(resetProbability=0.15, maxIter=10)

In [20]:
ranks.edges.limit(5).toPandas()

src                     dst                  name_song  sum_ms  \
0    1150346509  7GoQIEDTGyYLKgQv4XGkxO                  Barcelona  157000   
1  constbraga99  3JOF9NzQVkUXtCcJbEQuAb           Heart Like Yours  199960   
2  constbraga99  0sfplmtNjPcLVL6W498iK2  Cucurrucucú Paloma - Live  266413   
3  constbraga99  0nygLn6lMItG4bKFiGTdNx   Esta Noite o Amor Chegou  178306   
4  constbraga99  4DEldV3wQKjbMRhVw64bg6                       Raro  199093   

   count    weight  
0      1  0.010000  
1      1  0.001916  
2      1  0.001916  
3      1  0.001916  
4      1  0.001916

### The most popular songs in our master are....... 🥁🥁🥁🥁🥁🥁🥁

1. 212
2. Mon Amour
3. Dusk Till Dawn (feat. Sia) - Radio Ed
4. Pepas
5. 2U (feat. Justin Bieber)

It works! When Mon Amour (Remix) or Pepas sounds in a club, is when people get more excited.  

In [21]:
# Since we do not have the name of the song we will do a join with our songs table
ranks_vertices = (ranks.vertices).join(aux_songs, "id") \
                  .orderBy(desc("pagerank"))\
                  .select("id", "name_song", "pagerank") \
                  
ranks_vertices.limit(5).toPandas()

id                                name_song  pagerank
0  6no1mklq4BJBg7KJ6Dly7N                                      212  1.846876
1  5TMLavqGRKNxgzMBrVpC9R                        Mon Amour - Remix  1.017766
2  1j4kHkkpqZRBwE0A4CN4Yv  Dusk Till Dawn (feat. Sia) - Radio Edit  1.016187
3  5fwSHlTEWpluwOM0Sxnh5k                                    Pepas  1.013334
4  3A7qX2QjDlPnazUsRk5y0M                 2U (feat. Justin Bieber)  1.013215

In [22]:
ranks_vertices.describe().toPandas()

summary                      id name_song              pagerank
0   count                   12036     12036                 12036
1    mean                    None  Infinity     1.000003367269801
2  stddev                    None       NaN  0.007884850768133198
3     min  001cDNNoKfOqN8S1tdDDAL              0.9988161117065335
4     max  7zwNm7iRofQJ0PsiFIDu8a      Друг    1.8468759312605543

# Part 2.  Analytics: song features

Once we have the page rank of our songs we will use it as a target variable  for our model. Our goal will be to predict its value based on song features taken from Spotify. 

In [23]:
from pyspark.ml import Pipeline
from pyspark.sql.functions import isnull, when, count, col
from pyspark.ml.feature import OneHotEncoder, StringIndexer
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler

In [24]:
song_features = (spark.read
            .option("header","true")
            .option("inferSchema","true")
            .json("hdfs://localhost:9000/datalake/raw/spotify/song_features/"))

The meaning of each one of the features of a song can be found in the Spotify API documentation https://developer.spotify.com/documentation/web-api/reference/#/operations/get-audio-features


In [25]:
song_features.printSchema()

root
 |-- audio_features: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- acousticness: double (nullable = true)
 |    |    |-- analysis_url: string (nullable = true)
 |    |    |-- danceability: double (nullable = true)
 |    |    |-- duration_ms: long (nullable = true)
 |    |    |-- energy: double (nullable = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- instrumentalness: double (nullable = true)
 |    |    |-- key: long (nullable = true)
 |    |    |-- liveness: double (nullable = true)
 |    |    |-- loudness: double (nullable = true)
 |    |    |-- mode: long (nullable = true)
 |    |    |-- speechiness: double (nullable = true)
 |    |    |-- tempo: double (nullable = true)
 |    |    |-- time_signature: long (nullable = true)
 |    |    |-- track_href: string (nullable = true)
 |    |    |-- type: string (nullable = true)
 |    |    |-- uri: string (nullable = true)
 |    |    |-- valence: double (nullable = true)



We want to have one row per song, to accomplish that we will use the explode function. (Same as we did in the previous section)

In [26]:
song_features = song_features.selectExpr('explode(audio_features) as struct_features')

song_features.count()

13116

We are analyzing a total of 13116 songs

In [27]:
song_features.limit(5).toPandas()

struct_features
0     (0.163, https://api.spotify.com/v1/audio-analysis/7wUgqu8PYOpixMpgxVQnW8, 0.655, 453621, 0.878, 7wUgqu8PYOpixMpgxVQnW8, 0.829, 2, 0.0658, -9.752, 1, 0.0707, 124.915, 4, https://api.spotify.com/v1/tracks/7wUgqu8PYOpixMpgxVQnW8, audio_features, spotify:track:7wUgqu8PYOpixMpgxVQnW8, 0.898)
1       (0.537, https://api.spotify.com/v1/audio-analysis/7mcXIUAFcLyusghJHgki2g, 0.762, 274486, 0.905, 7mcXIUAFcLyusghJHgki2g, 0.763, 9, 0.368, -7.902, 0, 0.0964, 122.51, 4, https://api.spotify.com/v1/tracks/7mcXIUAFcLyusghJHgki2g, audio_features, spotify:track:7mcXIUAFcLyusghJHgki2g, 0.455)
2   (8.71e-06, https://api.spotify.com/v1/audio-analysis/1yGwvJ0DPO3k7YceNGjbFT, 0.72, 366294, 0.858, 1yGwvJ0DPO3k7YceNGjbFT, 0.842, 4, 0.694, -9.228, 0, 0.0383, 140.007, 4, https://api.spotify.com/v1/tracks/1yGwvJ0DPO3k7YceNGjbFT, audio_features, spotify:track:1yGwvJ0DPO3k7YceNGjbFT, 0.0525)
3  (0.00227, https://api.spotify.com/v1/audio-analysis/6frBQATToJ7MOiVwJS1Ij7, 0.626, 430010, 0.779, 6frBQATToJ7MOiVwJS1Ij7, 0.426, 1, 0.0732, -12.351, 1, 0.0316, 136.029, 4, https://api.spotify.com/v1/tracks/6frBQATToJ7MOiVwJS1Ij7, audio_features, spotify:track:6frBQATToJ7MOiVwJS1Ij7, 0.389)
4    (0.00186, https://api.spotify.com/v1/audio-analysis/4JYK94KKCpZsd6CspWOm5E, 0.411, 320709, 0.957, 4JYK94KKCpZsd6CspWOm5E, 0.838, 1, 0.0861, -9.748, 1, 0.0787, 84.737, 3, https://api.spotify.com/v1/tracks/4JYK94KKCpZsd6CspWOm5E, audio_features, spotify:track:4JYK94KKCpZsd6CspWOm5E, 0.209)

We put all the fields of the struct in columns

In [28]:
song_features = song_features.select(col('struct_features.*'))
song_features.limit(5).toPandas()

acousticness  \
0      0.163000   
1      0.537000   
2      0.000009   
3      0.002270   
4      0.001860   

                                                       analysis_url  \
0  https://api.spotify.com/v1/audio-analysis/7wUgqu8PYOpixMpgxVQnW8   
1  https://api.spotify.com/v1/audio-analysis/7mcXIUAFcLyusghJHgki2g   
2  https://api.spotify.com/v1/audio-analysis/1yGwvJ0DPO3k7YceNGjbFT   
3  https://api.spotify.com/v1/audio-analysis/6frBQATToJ7MOiVwJS1Ij7   
4  https://api.spotify.com/v1/audio-analysis/4JYK94KKCpZsd6CspWOm5E   

   danceability  duration_ms  energy                      id  \
0         0.655       453621   0.878  7wUgqu8PYOpixMpgxVQnW8   
1         0.762       274486   0.905  7mcXIUAFcLyusghJHgki2g   
2         0.720       366294   0.858  1yGwvJ0DPO3k7YceNGjbFT   
3         0.626       430010   0.779  6frBQATToJ7MOiVwJS1Ij7   
4         0.411       320709   0.957  4JYK94KKCpZsd6CspWOm5E   

   instrumentalness  key  liveness  loudness  mode  speechiness    tempo  \
0             0.829    2    0.0658    -9.752     1       0.0707  124.915   
1             0.763    9    0.3680    -7.902     0       0.0964  122.510   
2             0.842    4    0.6940    -9.228     0       0.0383  140.007   
3             0.426    1    0.0732   -12.351     1       0.0316  136.029   
4             0.838    1    0.0861    -9.748     1       0.0787   84.737   

   time_signature                                                track_href  \
0               4  https://api.spotify.com/v1/tracks/7wUgqu8PYOpixMpgxVQnW8   
1               4  https://api.spotify.com/v1/tracks/7mcXIUAFcLyusghJHgki2g   
2               4  https://api.spotify.com/v1/tracks/1yGwvJ0DPO3k7YceNGjbFT   
3               4  https://api.spotify.com/v1/tracks/6frBQATToJ7MOiVwJS1Ij7   
4               3  https://api.spotify.com/v1/tracks/4JYK94KKCpZsd6CspWOm5E   

             type                                   uri  valence  
0  audio_features  spotify:track:7wUgqu8PYOpixMpgxVQnW8   0.8980  
1  audio_features  spotify:track:7mcXIUAFcLyusghJHgki2g   0.4550  
2  audio_features  spotify:track:1yGwvJ0DPO3k7YceNGjbFT   0.0525  
3  audio_features  spotify:track:6frBQATToJ7MOiVwJS1Ij7   0.3890  
4  audio_features  spotify:track:4JYK94KKCpZsd6CspWOm5E   0.2090

We will join the features dataset with the one after the page rank, so we can have the page rank as column (that we will use later as a target variable)

In [29]:
song_features = (song_features).join(ranks_vertices, "id")
song_features.limit(3).toPandas()

id  acousticness  \
0  3VoZIN3MSxpLKP0LdsTHqj       0.03260   
1  4KuSic9vPLVLgB5lCfeFQy       0.57100   
2  5G6INMRilGSstvrHgvfYPj       0.00676   

                                                       analysis_url  \
0  https://api.spotify.com/v1/audio-analysis/3VoZIN3MSxpLKP0LdsTHqj   
1  https://api.spotify.com/v1/audio-analysis/4KuSic9vPLVLgB5lCfeFQy   
2  https://api.spotify.com/v1/audio-analysis/5G6INMRilGSstvrHgvfYPj   

   danceability  duration_ms  energy  instrumentalness  key  liveness  \
0         0.420       333309   0.584          0.075900   11     0.262   
1         0.533       170795   0.538          0.000002   10     0.101   
2         0.382       264824   0.928          0.014600    7     0.252   

   loudness  mode  speechiness    tempo  time_signature  \
0    -8.388     0       0.0311  126.955               4   
1    -7.764     1       0.0984   87.887               4   
2    -4.547     1       0.0402  173.975               4   

                                                 track_href            type  \
0  https://api.spotify.com/v1/tracks/3VoZIN3MSxpLKP0LdsTHqj  audio_features   
1  https://api.spotify.com/v1/tracks/4KuSic9vPLVLgB5lCfeFQy  audio_features   
2  https://api.spotify.com/v1/tracks/5G6INMRilGSstvrHgvfYPj  audio_features   

                                    uri  valence                  name_song  \
0  spotify:track:3VoZIN3MSxpLKP0LdsTHqj    0.086                Electricity   
1  spotify:track:4KuSic9vPLVLgB5lCfeFQy    0.482             pa' que sueñes   
2  spotify:track:5G6INMRilGSstvrHgvfYPj    0.055  Hold On - Sub Focus Remix   

   pagerank  
0  0.999216  
1  0.998945  
2  0.999401

In [30]:
song_features=song_features.withColumn("key", song_features["key"].cast("string")) 
song_features.dtypes

[('id', 'string'),
 ('acousticness', 'double'),
 ('analysis_url', 'string'),
 ('danceability', 'double'),
 ('duration_ms', 'bigint'),
 ('energy', 'double'),
 ('instrumentalness', 'double'),
 ('key', 'string'),
 ('liveness', 'double'),
 ('loudness', 'double'),
 ('mode', 'bigint'),
 ('speechiness', 'double'),
 ('tempo', 'double'),
 ('time_signature', 'bigint'),
 ('track_href', 'string'),
 ('type', 'string'),
 ('uri', 'string'),
 ('valence', 'double'),
 ('name_song', 'string'),
 ('pagerank', 'double')]

In [31]:
song_features.count()

13114

### Lets do some Exploratory Data analysis
describe() will tell us if there is any null value

In [32]:
song_features.describe().toPandas()

summary                      id         acousticness  \
0   count                   13114                13114   
1    mean                    None  0.25299145833002884   
2  stddev                    None  0.27053308610826543   
3     min  001cDNNoKfOqN8S1tdDDAL              1.33E-6   
4     max  7zwNm7iRofQJ0PsiFIDu8a                0.996   

                                                       analysis_url  \
0                                                             13114   
1                                                              None   
2                                                              None   
3  https://api.spotify.com/v1/audio-analysis/001cDNNoKfOqN8S1tdDDAL   
4  https://api.spotify.com/v1/audio-analysis/7zwNm7iRofQJ0PsiFIDu8a   

          danceability         duration_ms               energy  \
0                13114               13114                13114   
1   0.6526813253012045  234119.55490315694    0.668128651059936   
2  0.14812390494477357   67910.12812234153  0.20417036952146433   
3                  0.0                4520              0.00229   
4                0.991             1440000                  1.0   

      instrumentalness                 key             liveness  ...  \
0                13114               13114                13114  ...   
1  0.08014111488943115    5.33422296782065  0.18420420924203146  ...   
2  0.22691159021991192  3.6132113592622708  0.15953315463666745  ...   
3                  0.0                   0                  0.0  ...   
4                0.985                   9                0.995  ...   

                 mode          speechiness               tempo  \
0               13114                13114               13114   
1  0.6255909714808602   0.0876198566417569   120.1106157541559   
2  0.4839883986970017  0.08546183885337708  28.434323476841545   
3                   0                  0.0                 0.0   
4                   1                0.918             218.971   

       time_signature  \
0               13114   
1  3.9596614305322557   
2  0.3019624792608878   
3                   0   
4                   5   

                                                 track_href            type  \
0                                                     13114           13114   
1                                                      None            None   
2                                                      None            None   
3  https://api.spotify.com/v1/tracks/001cDNNoKfOqN8S1tdDDAL  audio_features   
4  https://api.spotify.com/v1/tracks/7zwNm7iRofQJ0PsiFIDu8a  audio_features   

                                    uri              valence  \
0                                 13114                13114   
1                                  None   0.5603843373493977   
2                                  None  0.23873884306219773   
3  spotify:track:001cDNNoKfOqN8S1tdDDAL                  0.0   
4  spotify:track:7zwNm7iRofQJ0PsiFIDu8a                0.985   

                        name_song             pagerank  
0                           13114                13114  
1                        Infinity   1.0002881211844574  
2                             NaN  0.00763943136615224  
3                                   0.9988161117065335  
4  Étranges nuages - Yuksek Remix   1.8468759312605543  

[5 rows x 21 columns]

Seems that we do not have null values (all columns have 13114 elements). Lets double check it



In [33]:

song_features.select([count(when(isnull(c), c)).alias(c) for c in song_features.columns]).toPandas()


id  acousticness  analysis_url  danceability  duration_ms  energy  \
0   0             0             0             0            0       0   

   instrumentalness  key  liveness  loudness  mode  speechiness  tempo  \
0                 0    0         0         0     0            0      0   

   time_signature  track_href  type  uri  valence  name_song  pagerank  
0               0           0     0    0        0          0         0

Amazing, **there are no null values!**


Even though we do not have null values, the 'key' column that represents the music key (Do = 1, Re=2 etc..) in which
the song is, has the value -1 in case the algoritm is not able to represent it. Lets check it.  

In [34]:
song_features.select("*").where("key<0").limit(5).toPandas()
# awesome no 'key' values with -1

Empty DataFrame
Columns: [id, acousticness, analysis_url, danceability, duration_ms, energy, instrumentalness, key, liveness, loudness, mode, speechiness, tempo, time_signature, track_href, type, uri, valence, name_song, pagerank]
Index: []

### Feature Engineering

We drop the features that won't contribute to the algorithm.

In [35]:
song_features = song_features.drop('analysis_url', 'track_href', 'type', 'uri', 'name_song', 'id' )
song_features.limit(1).toPandas()

acousticness  danceability  duration_ms  energy  instrumentalness key  \
0        0.0326          0.42       333309   0.584            0.0759  11   

   liveness  loudness  mode  speechiness    tempo  time_signature  valence  \
0     0.262    -8.388     0       0.0311  126.955               4    0.086   

   pagerank  
0  0.999216

The only categorical variable that we have is key, where we will  apply OneHotEncoder.

In [36]:

categoricalCols = ['key']
numericCols = [field for (field, dataType) in song_features.dtypes if (((dataType == "double") | (dataType == "bigint"))
                                                                    & (field != "pagerank"))]

indexOutputCols = [x + "Index" for x in categoricalCols]
oheOutputCols = [x + "OHE" for x in categoricalCols]
stringIndexer = StringIndexer(inputCols=categoricalCols, outputCols=indexOutputCols,handleInvalid="skip")

oheEncoder = OneHotEncoder(inputCols=indexOutputCols,outputCols=oheOutputCols)
assemblerInputs = (oheOutputCols + numericCols)
print("Feature columns: ",assemblerInputs)

Feature columns:  ['keyOHE', 'acousticness', 'danceability', 'duration_ms', 'energy', 'instrumentalness', 'liveness', 'loudness', 'mode', 'speechiness', 'tempo', 'time_signature', 'valence']


Assembling features into a vector

In [37]:
vecAssembler = VectorAssembler(inputCols=assemblerInputs,outputCol="features")

Adding a standard scaler to scale our features

In [38]:
sScaler = StandardScaler().setInputCol("features").setOutputCol("scaled_features")

 Testing our pipeline. It works, our target column will be scaled_features

In [39]:
test_pipeline = Pipeline(stages = [stringIndexer, oheEncoder ,vecAssembler, sScaler])
features_df = test_pipeline.fit(song_features).transform(song_features)
features_df.limit(2).toPandas()


acousticness  danceability  duration_ms  energy  instrumentalness key  \
0        0.0326         0.420       333309   0.584          0.075900  11   
1        0.5710         0.533       170795   0.538          0.000002  10   

   liveness  loudness  mode  speechiness    tempo  time_signature  valence  \
0     0.262    -8.388     0       0.0311  126.955               4    0.086   
1     0.101    -7.764     1       0.0984   87.887               4    0.482   

   pagerank  keyIndex  \
0  0.999216       5.0   
1  0.998945      10.0   

                                                    keyOHE  \
0  (0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0)   
1  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0)   

                                                                                                                                           features  \
0   (0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0326, 0.42, 333309.0, 0.584, 0.0759, 0.262, -8.388, 0.0, 0.0311, 126.955, 4.0, 0.086)   
1  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.571, 0.533, 170795.0, 0.538, 1.88e-06, 0.101, -7.764, 1.0, 0.0984, 87.887, 4.0, 0.482)   

                                                                                                                                                                                                                                                                                                           scaled_features  
0                 (0.0, 0.0, 0.0, 0.0, 0.0, 3.608759053987601, 0.0, 0.0, 0.0, 0.0, 0.0, 0.12050282081561628, 2.8354639999302784, 4.908089694655512, 2.8603562866089836, 0.33449150802055255, 1.6422918521024557, -2.1672274389082804, 0.0, 0.36390511153588445, 4.46485038068161, 13.246678891333728, 0.36022625768356736)  
1  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 4.024335804654814, 2.1106475670465303, 3.5983388380067582, 2.5150151343008686, 2.6350542503349885, 8.285165152551236e-06, 0.6330972406959848, -2.006003080076763, 2.0661652277042384, 1.1513910924479431, 3.090877125020398, 13.246678891333728, 2.0189425139939474)


Now that we know that our pipeline works it is time to train our model. We are going to use **Linear Regression** since the target variable (the pageRank) is a continous one. 


In [40]:
from pyspark.ml.regression import LinearRegression

lr = LinearRegression(labelCol="pagerank", featuresCol="scaled_features").setElasticNetParam(0.8) #adding penalty


In [41]:
def create_pipeline(classifier):
    return Pipeline(stages = [stringIndexer, oheEncoder, vecAssembler, sScaler ,classifier])
pipeline = create_pipeline(lr)

In [42]:
(trainingData, testData) = song_features.randomSplit([0.8,0.2],seed=42)

In [43]:
model = pipeline.fit(trainingData)

Once the model is trained, it is time to predict using our test dataset. 

In [44]:
prediction_df = model.transform(testData)
prediction_df.limit(5).toPandas()

acousticness  danceability  duration_ms  energy  instrumentalness key  \
0       0.00267         0.773       256813   0.572          0.000002   8   
1       0.00676         0.382       264824   0.928          0.014600   7   
2       0.00991         0.672       252162   0.441          0.000007   1   
3       0.01690         0.596       203418   0.854          0.000000   7   
4       0.03560         0.634       172131   0.861          0.000000  10   

   liveness  loudness  mode  speechiness    tempo  time_signature  valence  \
0    0.0727    -6.802     0       0.0898  140.336               4    0.876   
1    0.2520    -4.547     1       0.0402  173.975               4    0.055   
2    0.1090    -9.065     0       0.0268  115.059               4    0.429   
3    0.1240    -5.114     0       0.4630  120.274               4    0.152   
4    0.0831    -4.580     1       0.1070  121.903               4    0.569   

   pagerank  keyIndex  \
0  0.998959       8.0   
1  0.999401       1.0   
2  1.000860       2.0   
3  1.000148       1.0   
4  0.999046      10.0   

                                                    keyOHE  \
0  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0)   
1  (0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0)   
2  (0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0)   
3  (0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0)   
4  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0)   

                                                                                                                                               features  \
0  (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.00267, 0.773, 256813.0, 0.572, 1.84e-06, 0.0727, -6.802, 0.0, 0.0898, 140.336, 4.0, 0.876)   
1     (0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00676, 0.382, 264824.0, 0.928, 0.0146, 0.252, -4.547, 1.0, 0.0402, 173.975, 4.0, 0.055)   
2    (0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.00991, 0.672, 252162.0, 0.441, 6.7e-06, 0.109, -9.065, 0.0, 0.0268, 115.059, 4.0, 0.429)   
3          (0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0169, 0.596, 203418.0, 0.854, 0.0, 0.124, -5.114, 0.0, 0.463, 120.274, 4.0, 0.152)   
4          (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0356, 0.634, 172131.0, 0.861, 0.0, 0.0831, -4.58, 1.0, 0.107, 121.903, 4.0, 0.569)   

                                                                                                                                                                                                                                                                                                        scaled_features  \
0              (0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 3.921574954008466, 0.0, 0.0, 0.009909260741079668, 5.223300120692353, 3.7261933216026644, 2.813778565767055, 8.177766465027407e-06, 0.46205624762370157, -1.7686454462473553, 0.0, 1.0453812430833356, 4.947932879529432, 13.5719807892484, 3.6732154108025554)   
1  (0.0, 3.1745373305462468, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.025088615209624927, 2.5812427504585753, 3.842427837376239, 4.565011379426272, 0.06488879912467399, 1.601625507581469, -1.1823038582897272, 2.0649013110813916, 0.467976903919266, 6.133968637528025, 13.5719807892484, 0.23062425524445268)   
2                (0.0, 0.0, 3.2322363753823247, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0367793160839324, 4.540824943215085, 3.6587102691918676, 2.169364243886838, 2.977773658461067e-05, 0.6927665885967464, -2.3570671817454096, 0.0, 0.31198460261284405, 4.056722503033982, 13.5719807892484, 1.798869190906731)   
3                                  (0.0, 3.1745373305462468, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.06272153802406231, 4.027279265113379, 2.9514658256932895, 4.200991075463401, 0.0, 0.7881014402385006, -1.3297343152174323, 0.0, 5.389883246632343, 4.240591716683694, 13.5719807892484, 0.6373615781301237)   
4                        (0.0, 0.0, 0.0, 0.0, 0

In [45]:
prediction_df.describe().toPandas()

summary        acousticness         danceability         duration_ms  \
0   count                2657                 2657                2657   
1    mean  0.2575244503575459   0.6535111027474596  232904.54761008656   
2  stddev  0.2747782693304265  0.14867189900968658   63774.12931164106   
3     min             1.04E-5                0.144               49467   
4     max               0.996                0.987              837300   

                energy     instrumentalness                key  \
0                 2657                 2657               2657   
1   0.6682946480993598  0.08452600451637185  5.344373353406097   
2  0.20765546772699883    0.234274239367666  3.578713547594368   
3              0.00506                  0.0                  0   
4                0.997                0.977                  9   

              liveness            loudness                mode  \
0                 2657                2657                2657   
1  0.18711716221302221  -7.187538577342872  0.6300338727888596   
2  0.16788515820915745   3.965715519573949  0.4828860654082443   
3                0.015             -37.768                   0   
4                0.995              -0.787                   1   

           speechiness               tempo      time_signature  \
0                 2657                2657                2657   
1  0.08633635679337598  120.80688144523904  3.9537071885585244   
2  0.08371194038983014  28.709839214912108  0.3288957795525687   
3               0.0232              50.827                   1   
4                0.564             216.053                   5   

               valence              pagerank            keyIndex  \
0                 2657                  2657                2657   
1   0.5571882574331954    1.0002516062797073    4.54384644335717   
2  0.23976079995464544  0.001913910346955985  3.2385771158716627   
3               0.0358    0.9988161117065335                 0.0   
4                0.984    1.0177663316935412                11.0   

             prediction  
0                  2657  
1    1.0003014643027408  
2  5.347447014796846E-4  
3    0.9986105224736108  
4    1.0025105977419366

What is the optimal PageRank value from which the students of the master will like the song? 


Lets do an small test. One of the most popular songs when we computed the PageRank was Mon Amour (Remix) from the Spanish singer Aitana. Lets see what is the predicted PageRank value for the same song but without remix. 

In [46]:
#1.017766 real with remix (Aitana) vs 1.000894 pred without remix (sin Aitana). 
# PThreshold PR > 1??
prueba_df = spark.read.json('hdfs://localhost:9000/datalake/raw/spotify/_test_/*')
prediction_df_aux = model.transform(prueba_df)
prediction_df_aux.limit(1).toPandas()

acousticness  \
0         0.403   

                                                       analysis_url  \
0  https://api.spotify.com/v1/audio-analysis/064ikblBFGS6HL35D71LZy   

   danceability  duration_ms  energy                      id  \
0          0.76       173836   0.616  064ikblBFGS6HL35D71LZy   

   instrumentalness  key  liveness  loudness  ...  time_signature  \
0           0.00053    2     0.107    -8.557  ...               4   

                                                 track_href            type  \
0  https://api.spotify.com/v1/tracks/064ikblBFGS6HL35D71LZy  audio_features   

                                    uri valence keyIndex  \
0  spotify:track:064ikblBFGS6HL35D71LZy   0.168      4.0   

                                                    keyOHE  \
0  (0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0)   

                                                                                                                                          features  \
0  (0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.403, 0.76, 173836.0, 0.616, 0.00053, 0.107, -8.557, 1.0, 0.0842, 116.027, 4.0, 0.168)   

                                                                                                                                                                                                                                                                                                        scaled_features  \
0  (0.0, 0.0, 0.0, 0.0, 3.6093489223438384, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.4956674451891785, 5.135456781017061, 2.5222498170035035, 3.0302230708260596, 0.00235555229699159, 0.6800552750445126, -2.2249778129283477, 2.0649013110813916, 0.9801904305970696, 4.090852013832241, 13.5719807892484, 0.7044522705648737)   

  prediction  
0   1.000894  

[1 rows x 23 columns]

Time to evaluate our model with CrossValidation. Be patient...

In [47]:

from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

lrg = LinearRegression()
params = ParamGridBuilder().addGrid(lrg.regParam, [0.1, 0.01]).build()

evaluator = RegressionEvaluator()\
  .setMetricName("rmse")\
  .setPredictionCol("prediction")\
  .setLabelCol("pagerank")
cv = CrossValidator()\
    .setEstimator(pipeline)\
    .setEvaluator(evaluator)\
    .setEstimatorParamMaps(params)\
    .setNumFolds(3)
  

model_cv = cv.fit(trainingData)
bestModel = model_cv.bestModel

In [48]:
from pyspark.mllib.evaluation import RegressionMetrics
out = bestModel.transform(testData)\
  .select("prediction", "pagerank").rdd.map(lambda x: (float(x[0]), float(x[1])))
metrics = RegressionMetrics(out)
print("MSE: " + str(metrics.meanSquaredError))
print("RMSE: " + str(metrics.rootMeanSquaredError))
print("R-squared: " + str(metrics.r2))
print("MAE: " + str(metrics.meanAbsoluteError))
print("Explained variance: " + str(metrics.explainedVariance))

MSE: 3.6920116589680775e-06
RMSE: 0.001921460813799771
R-squared: -0.008285140547086955
MAE: 0.0012972865262480065
Explained variance: 2.883300963405146e-07


Once we have picked the best model from the cross validation we will save it in HDFS to use it in Streaming

In [49]:
modelPath = "hdfs://localhost:9000/datalake/raw/spotify/model_registry"
bestModel.write().overwrite().save(modelPath)

In [52]:
# We will also save in the std layer the tracks DF in parquet. 

prediction_df.write.mode("overwrite").parquet("hdfs://localhost:9000/datalake/std/spotify/songs/predictions/")
ranks_vertices.repartition(1).write.format("com.databricks.spark.csv").option("header", "true").save("hdfs://localhost:9000/datalake/std/spotify/songs/vertices/")

## Part 3. Streaming.

Here is where the fun comes. 
1. We will load our previoulsy created model.
2. Kafka will produce the current song that the user is listening to. 
3. Kafka will produce in a second toppic the features of that song
4. Spark will consume the features of the song, and will apply the algorithm in real time. 
5. If the predicted PR is > 1 spark will send that song to a kafka oproducer who will add it to a playlist. 

Before running the code make sure you have loaded the oauth file, and that the kafka producer and consumer are running

In [53]:
# Loading the model
modelPath = "hdfs://localhost:9000/datalake/raw/spotify/model_registry"
from pyspark.ml import PipelineModel
savedModel = PipelineModel.load(modelPath)

In [ ]:
from pyspark.sql.functions import col, split, window
spotify_str_df = spark.readStream\
               .format("kafka") \
               .option("kafka.bootstrap.servers", "localhost:9092") \
               .option("subscribe", "spotify_mbd") \
               .option("startingOffsets", "latest") \
               .option("kafka.group.id", "IE") \
               .load()
spotify_str_df

In [ ]:
spotify_features_df = spark.readStream\
               .format("kafka") \
               .option("kafka.bootstrap.servers", "localhost:9092") \
               .option("subscribe", "spotify_mbd_features") \
               .option("startingOffsets", "latest") \
               .option("kafka.group.id", "IE1").load()
spotify_features_df

In [ ]:
from pyspark.sql.types import TimestampType

spotify_current = spotify_str_df.selectExpr("timestamp", "CAST(value AS STRING) as data_str")\
               .select("timestamp", split("data_str",'\|').alias("fields"))\
               .selectExpr("fields[0] as name_song", 
                           "fields[1] as artist_name",  
                           "fields[3] as id",
                           "timestamp")\
                .withWatermark("timestamp", "40 seconds")\
                .dropDuplicates(["id"])\
              # .writeStream\
               #.format("console")\
               #.outputMode("append")\
               #.trigger(processingTime='20 seconds')\
               #.start()\
               #.awaitTermination()
                # This will go to a real time dashboard
               # .groupBy(window(col("timestamp"), "30 seconds"), "id", "name_song", "artist_name", "timestamp").count()\



we innfer the json schema from this example

In [ ]:
from pyspark.sql import DataFrame
dict_schema = {'danceability': 0.76,
 'energy': 0.616,
 'key': 2,
 'loudness': -8.557,
 'mode': 1,
 'speechiness': 0.0842,
 'acousticness': 0.403,
 'instrumentalness': 0.00053,
 'liveness': 0.107,
 'valence': 0.168,
 'tempo': 116.027,
 'type': 'audio_features',
 'id': '064ikblBFGS6HL35D71LZy',
 'uri': 'spotify:track:064ikblBFGS6HL35D71LZy',
 'track_href': 'https://api.spotify.com/v1/tracks/064ikblBFGS6HL35D71LZy',
 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/064ikblBFGS6HL35D71LZy',
 'duration_ms': 173836,
 'time_signature': 4}

df_schema = spark.createDataFrame([list(dict_schema.values())], list(dict_schema.keys()))
schema = df_schema.schema

In [ ]:
from pyspark.sql.functions import from_json, col

spotify_features = spotify_features_df.selectExpr("timestamp", "CAST(value AS STRING) as data_str")\
            .select("timestamp", from_json("data_str", schema).alias("values"))\
            .select("timestamp", col('values.*')).drop("analysis_url").drop("track_href").drop("uri")\
            #.writeStream\
            #.format("console")\
            #.outputMode("append")\
            #.trigger(processingTime='5 seconds')\
            #.start()\
            #.awaitTermination()
            # Anadir .withColumn("event_time",col("timestamp_str").cast(TimestampType())) 
            # .groupBy(window, col("timestamp", "30 seconds"), "id")
            # from pyspark.sql.types import TimestampType
            #            .withWatermark("timestamp", "15 seconds")\



In [ ]:
#join_df = spotify_current.join(spotify_features,"id")

In [ ]:
predictions = savedModel.transform(spotify_features)

**Serving!** For batch, we serve the static tracks DF to serve it in MariaDB. 

Bonus point: We have replicated our db  using our student subscrition in Azure so we can have a dashboard with the insights. 😃

In [ ]:
tracks.dtypes

In [ ]:
def write_to_db(df):    
    # 
    # Cloud credentials
    #url = "jdbc:mariadb://osbdet-mariadb.mariadb.database.azure.com:3306/Spotify"
    #props = {"user": "moderndata@osbdet-mariadb,
    #         "password":"Osbdet123$", 
    #         "driver":"org.mariadb.jdbc.Driver"}
    table = "Tracks"
    mode = "append"
    url = "jdbc:mariadb://localhost:3306/Spotify"
    props = {"user": "osbdet",
             "password":"osbdet123$", 
             "driver":"org.mariadb.jdbc.Driver"}
    df.select('playlist_id', 
              'followers', 
              'owner_id', 
              'playlist_name', 
              'user_playlist_id', 
              'user_name', 'name_song', 'artists_names', 'song_id', 'popularity',
              'duration_ms').write.jdbc(url,table,mode,props)
     

In [ ]:
write_to_db(tracks)

**Streaming Serving:** If the predicted value is > 1 we will send it to kafka who will add it to the playlist inside spotify  (execute consumer)

https://open.spotify.com/playlist/4JJmlxODSah5VYAoqGeOqR

In [ ]:
predictions.where("prediction>1").selectExpr("id as value").writeStream \
       .format("kafka") \
       .option("kafka.bootstrap.servers", "localhost:9092") \
       .option("checkpointLocation", "/tmp/spark_checkpoint") \
       .option("topic", "send_to_playlist") \
       .start() \
       .awaitTermination()

In [ ]:
#predictions.select("id", "prediction").where("prediction>1").writeStream\
#       .format("console")\
#       .outputMode("append")\
#        .option("truncate", False)\
#        .option("numRows", 10)\
#        .trigger(processingTime='20 seconds')\
#        .start()\
#        .awaitTermination()